In [1]:
from gurobipy import *

In [2]:
m = Model("clique")

Using license file /Users/melkebir/gurobi.lic
Academic license - for non-commercial use only


In [3]:
x1 = m.addVar(vtype=GRB.BINARY, name="v_1")
x2 = m.addVar(vtype=GRB.BINARY, name="v_2")
x3 = m.addVar(vtype=GRB.BINARY, name="v_3")
x4 = m.addVar(vtype=GRB.BINARY, name="v_4")

In [4]:
m.addConstr(x2+x3 <= 1)

<gurobi.Constr *Awaiting Model Update*>

In [5]:
m.setObjective(x1 + x2 + x3 + x4, GRB.MAXIMIZE)

In [6]:
m.optimize()

Gurobi Optimizer version 9.0.1 build v9.0.1rc0 (mac64)
Optimize a model with 1 rows, 4 columns and 2 nonzeros
Model fingerprint: 0xa71d988c
Variable types: 0 continuous, 4 integer (4 binary)
Coefficient statistics:
  Matrix range     [1e+00, 1e+00]
  Objective range  [1e+00, 1e+00]
  Bounds range     [1e+00, 1e+00]
  RHS range        [1e+00, 1e+00]
Found heuristic solution: objective 3.0000000
Presolve removed 1 rows and 4 columns
Presolve time: 0.01s
Presolve: All rows and columns removed

Explored 0 nodes (0 simplex iterations) in 0.04 seconds
Thread count was 1 (of 4 available processors)

Solution count 1: 3 

Optimal solution found (tolerance 1.00e-04)
Best objective 3.000000000000e+00, best bound 3.000000000000e+00, gap 0.0000%


In [8]:
for v in m.getVars():
    print(v.varName, v.x)

v_1 1.0
v_2 1.0
v_3 0.0
v_4 1.0


In [9]:
def parse_DIMACS(filename, relax):
    edges = set()
    with open(filename) as f:
        for line in f:
            if line.startswith('p'):
                nrVertices = int(line.rstrip("\n").split()[-2])
            elif line.startswith('e'):
                u = int(line.rstrip("\n").split()[-2])-1
                v = int(line.rstrip("\n").split()[-1])-1
                edges |= set([(u,v)])
    m = Model(filename)
    t = GRB.CONTINUOUS if relax else GRB.BINARY
    x = m.addVars(range(nrVertices), vtype=t)
    m.update()
    for i in range(nrVertices):
        for j in range(i+1, nrVertices):
            if ((i,j) not in edges) and ((j,i) not in edges):
                m.addConstr(x[i] + x[j] <= 1)
    if relax:
        for i in range(nrVertices):
            m.addConstr(0<=x[i]<=1)
    m.update()
    m.setObjective(quicksum(x[i] for i in range(nrVertices)), GRB.MAXIMIZE)
    m.update()
    return m, nrVertices

In [10]:
m, nrVertices = parse_DIMACS("./C125.9.clq.txt", False)

In [40]:
m.optimize()
for v in m.getVars():
    if v.x > 0:
        print(v.varName, v.x)

Optimize a model with 787 rows, 125 columns and 1574 nonzeros
Variable types: 0 continuous, 125 integer (125 binary)
Coefficient statistics:
  Matrix range     [1e+00, 1e+00]
  Objective range  [1e+00, 1e+00]
  Bounds range     [1e+00, 1e+00]
  RHS range        [1e+00, 1e+00]
Found heuristic solution: objective 26.0000000
Presolve removed 312 rows and 0 columns
Presolve time: 0.01s
Presolved: 475 rows, 125 columns, 1217 nonzeros
Variable types: 0 continuous, 125 integer (125 binary)

Root relaxation: objective 4.322903e+01, 343 iterations, 0.03 seconds

    Nodes    |    Current Node    |     Objective Bounds      |     Work
 Expl Unexpl |  Obj  Depth IntInf | Incumbent    BestBd   Gap | It/Node Time

     0     0   43.22903    0  124   26.00000   43.22903  66.3%     -    0s
H    0     0                      27.0000000   43.22903  60.1%     -    0s
     0     0   42.87605    0  122   27.00000   42.87605  58.8%     -    0s
     0     0   42.52044    0  125   27.00000   42.52044  57.5%  